# Obtain

In [1]:
## Import necessary libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import datetime as dt

In [2]:
## Set options for displaying Pandas DataFrames
pd.options.display.max_columns = 100
pd.options.display.max_rows = 120

In [3]:
## Load in NC statewide voter history and info by election
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs.zip',
                          dtype={'precinct_abbrv': str, 
                              'super_court_abbrv': str, 
                              'judic_dist_abbrv': str,
                              'school_dist_abbrv': str,
                              'vtd_abbrv': str
                                })
voter_elecs.head()

ParserError: Error tokenizing data. C error: Calling read(nbytes) on source failed. Try engine='python'.

# Scrub and Explore

In [4]:
## Check metadata for df
voter_elecs.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 44493612 entries, 0 to 44493611
Data columns (total 38 columns):
 #   Column                    Non-Null Count     Dtype  
---  ------                    --------------     -----  
 0   ncid                      44493612 non-null  object 
 1   election_desc             44493612 non-null  object 
 2   county_id                 20094199 non-null  float64
 3   voter_reg_num             20094199 non-null  float64
 4   election_lbl              20094199 non-null  object 
 5   voting_method             20094199 non-null  object 
 6   voted_party_cd            20085899 non-null  object 
 7   pct_label                 20094199 non-null  object 
 8   voted_county_id           20094199 non-null  float64
 9   vtd_label                 19581211 non-null  object 
 10  voter_status_desc         44493612 non-null  object 
 11  voter_status_reason_desc  44493606 non-null  object 
 12  last_name                 44492592 non-null  object 
 13  first_name

## Drop Duplicate Records

In [5]:
## Check for duplicate entries
voter_elecs.duplicated().sum()

0

In [6]:
## Inspect duplicate entries in voter history data
# voter_elecs.loc[voter_elecs.duplicated()]

In [7]:
## Remove duplicate entries from records of voter history
# voter_elecs.drop_duplicates(inplace=True)

In [7]:
## Check length of new df
len(voter_elecs)

44493612

In [8]:
## Check the intended length of the new df if every unique ncid
  ## appears only once for each election description
voter_elecs['ncid'].nunique() * voter_elecs['election_desc'].nunique()

44493228

In [9]:
44493612 - 44493228

384

In [10]:
## There are 384 instances where an ncid shows up as casting a vote
  ## more than once in the same election
voter_elecs.duplicated(subset=['ncid', 'election_desc']).sum()

384

In [11]:
## A total of 303 individuals show up more than once for a single election
dup_ncid_elecs = voter_elecs.loc[voter_elecs.duplicated(subset=['ncid', 'election_desc'], keep=False)]
display(dup_ncid_elecs.head())
dup_ncid_elecs['ncid'].nunique()

ncid       election_desc  county_id  voter_reg_num election_lbl  \
208220  AA16823  11/08/2016 GENERAL        1.0      2332350.0   11/08/2016   
208221  AA16823  11/08/2016 GENERAL        1.0      2332350.0   11/08/2016   
755957  AB22129  11/06/2012 GENERAL        2.0        25981.0   11/06/2012   
755958  AB22129  11/06/2012 GENERAL        2.0        25981.0   11/06/2012   
915381  AD28554  11/06/2018 GENERAL        4.0        31054.0   11/06/2018   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
208220         IN-PERSON            REP        02              1.0        02   
208221  ABSENTEE ONESTOP            DEM        LI             68.0        LI   
755957         IN-PERSON            REP        26             18.0        26   
755958  ABSENTEE ONESTOP            REP        B1              2.0        B1   
915381         IN-PERSON            REP        W1              4.0        W1   

       voter_status_desc voter_status_reason_desc last_name first_name  \
208220            ACTIVE                 VERIFIED     GANTT       JACK   
208221            ACTIVE                 VERIFIED     GANTT       JACK   
755957            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755958            ACTIVE                 VERIFIED    LYERLY    WINSTON   
915381            ACTIVE                 VERIFIED   KENDALL     ANDREW   

       middle_name  res_street_address res_city_desc state_cd  zip_code  \
208220     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208221     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
755957      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755958      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
915381     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   

       race_code ethnic_code party_cd gender_code  birth_age birth_state  \
208220         U          UN      REP           M         77          OR   
208221         U          UN      REP           M         77          OR   
755957         W          NL      UNA           M         50          NC   
755958         W          NL      UNA           M         50          NC   
915381         W          NL      UNA           M         26          NC   

       drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
208220           N  09/29/1973             02             13.0   
208221           N  09/29/1973             02             13.0   
755957           Y  09/20/1995             B1              5.0   
755958           Y  09/20/1995             B1              5.0   
915381           Y  12/28/2011          WADES              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
208220               15A              15A             24.0            64.0   
208221               15A              15A             24.0            64.0   
755957               22A              22A             42.0            94.0   
755958               22A              22A             42.0            94.0   
915381               16A              16A             25.0            55.0   

       school_dist_abbrv  dist_1_abbrv confidential_ind  birth_year vtd_abbrv  
208220               NaN          17.0                N        1943        02  
208221               NaN          17.0                N        1943        02  
755957               S01          32.0                N        1970        B1  
755958               S01          32.0                N        1970        B1  
915381              SCH7          21.0                N        1993        W1

303

In [12]:
## Examine the complete recent voting history of the 303 ncid's that show up 
  ## multiple times for a single election to investigate how the records differ
    ## and determine which record(s) to drop
for ncid in dup_ncid_elecs['ncid'].unique():
    display(voter_elecs.loc[voter_elecs['ncid']==ncid])

ncid       election_desc  county_id  voter_reg_num election_lbl  \
208218  AA16823  11/03/2020 GENERAL        1.0      2332350.0   11/03/2020   
208219  AA16823  11/06/2018 GENERAL        1.0      2332350.0   11/06/2018   
208220  AA16823  11/08/2016 GENERAL        1.0      2332350.0   11/08/2016   
208221  AA16823  11/08/2016 GENERAL        1.0      2332350.0   11/08/2016   
208222  AA16823  11/04/2014 GENERAL        1.0      2332350.0   11/04/2014   
208223  AA16823  11/06/2012 GENERAL        1.0      2332350.0   11/06/2012   
208224  AA16823                None        NaN            NaN          NaN   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
208218         IN-PERSON            REP        02              1.0        02   
208219         IN-PERSON            REP        02              1.0        02   
208220         IN-PERSON            REP        02              1.0        02   
208221  ABSENTEE ONESTOP            DEM        LI             68.0        LI   
208222         IN-PERSON            REP        02              1.0        02   
208223  ABSENTEE ONESTOP            REP        02              1.0        02   
208224               NaN            NaN       NaN              NaN       NaN   

       voter_status_desc voter_status_reason_desc last_name first_name  \
208218            ACTIVE                 VERIFIED     GANTT       JACK   
208219            ACTIVE                 VERIFIED     GANTT       JACK   
208220            ACTIVE                 VERIFIED     GANTT       JACK   
208221            ACTIVE                 VERIFIED     GANTT       JACK   
208222            ACTIVE                 VERIFIED     GANTT       JACK   
208223            ACTIVE                 VERIFIED     GANTT       JACK   
208224            ACTIVE                 VERIFIED     GANTT       JACK   

       middle_name  res_street_address res_city_desc state_cd  zip_code  \
208218     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208219     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208220     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208221     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208222     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208223     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   
208224     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   27215.0   

       race_code ethnic_code party_cd gender_code  birth_age birth_state  \
208218         U          UN      REP           M         77          OR   
208219         U          UN      REP           M         77          OR   
208220         U          UN      REP           M         77          OR   
208221         U          UN      REP           M         77          OR   
208222         U          UN      REP           M         77          OR   
208223         U          UN      REP           M         77          OR   
208224         U          UN      REP           M         77          OR   

       drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
208218           N  09/29/1973             02             13.0   
208219           N  09/29/1973             02             13.0   
208220           N  09/29/1973             02             13.0   
208221           N  09/29/1973             02             13.0   
208222           N  09/29/1973             02             13.0   
208223           N  09/29/1973             02             13.0   
208224           N  09/29/1973             02             13.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
208218               15A              15A             24.0            64.0   
208219               15A              15A             24.0            64.0   
208220               15A              15A             24.0            64.0   
208221               15A              15A             24.0            64.0   
208222               15

ncid       election_desc  county_id  voter_reg_num election_lbl  \
755953  AB22129  11/03/2020 GENERAL        2.0        25981.0   11/03/2020   
755954  AB22129  11/06/2018 GENERAL        2.0        25981.0   11/06/2018   
755955  AB22129  11/08/2016 GENERAL        2.0        25981.0   11/08/2016   
755956  AB22129  11/04/2014 GENERAL        2.0        25981.0   11/04/2014   
755957  AB22129  11/06/2012 GENERAL        2.0        25981.0   11/06/2012   
755958  AB22129  11/06/2012 GENERAL        2.0        25981.0   11/06/2012   
755959  AB22129                None        NaN            NaN          NaN   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
755953  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
755954  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
755955  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
755956  ABSENTEE ONESTOP            REP        B1              2.0        B1   
755957         IN-PERSON            REP        26             18.0        26   
755958  ABSENTEE ONESTOP            REP        B1              2.0        B1   
755959               NaN            NaN       NaN              NaN       NaN   

       voter_status_desc voter_status_reason_desc last_name first_name  \
755953            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755954            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755955            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755956            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755957            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755958            ACTIVE                 VERIFIED    LYERLY    WINSTON   
755959            ACTIVE                 VERIFIED    LYERLY    WINSTON   

       middle_name  res_street_address res_city_desc state_cd  zip_code  \
755953      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755954      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755955      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755956      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755957      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755958      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   
755959      COBURN  58  LINKSIDE LN          HICKORY       NC   28601.0   

       race_code ethnic_code party_cd gender_code  birth_age birth_state  \
755953         W          NL      UNA           M         50          NC   
755954         W          NL      UNA           M         50          NC   
755955         W          NL      UNA           M         50          NC   
755956         W          NL      UNA           M         50          NC   
755957         W          NL      UNA           M         50          NC   
755958         W          NL      UNA           M         50          NC   
755959         W          NL      UNA           M         50          NC   

       drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
755953           Y  09/20/1995             B1              5.0   
755954           Y  09/20/1995             B1              5.0   
755955           Y  09/20/1995             B1              5.0   
755956           Y  09/20/1995             B1              5.0   
755957           Y  09/20/1995             B1              5.0   
755958           Y  09/20/1995             B1              5.0   
755959           Y  09/20/1995             B1              5.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
755953               22A              22A             42.0            94.0   
755954               22A              22A             42.0            94.0   
755955               22A              22A             42.0            94.0   
755956               22A              22A             42.0            94.0   
755957               22

ncid       election_desc  county_id  voter_reg_num election_lbl  \
915380  AD28554  11/03/2020 GENERAL        4.0        31054.0   11/03/2020   
915381  AD28554  11/06/2018 GENERAL        4.0        31054.0   11/06/2018   
915382  AD28554  11/06/2018 GENERAL        4.0        31054.0   11/06/2018   
915383  AD28554  11/08/2016 GENERAL        4.0        31054.0   11/08/2016   
915384  AD28554  11/04/2014 GENERAL        4.0        31054.0   11/04/2014   
915385  AD28554  11/06/2012 GENERAL        4.0        31054.0   11/06/2012   
915386  AD28554                None        NaN            NaN          NaN   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
915380  ABSENTEE ONESTOP            UNA     WADES              4.0        W1   
915381         IN-PERSON            REP        W1              4.0        W1   
915382  ABSENTEE ONESTOP            DEM        W1              4.0        W1   
915383  ABSENTEE ONESTOP            DEM        W1              4.0        W1   
915384  ABSENTEE ONESTOP            REP        W1              4.0        W1   
915385         IN-PERSON            REP        W1              4.0        W1   
915386               NaN            NaN       NaN              NaN       NaN   

       voter_status_desc voter_status_reason_desc last_name first_name  \
915380            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915381            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915382            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915383            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915384            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915385            ACTIVE                 VERIFIED   KENDALL     ANDREW   
915386            ACTIVE                 VERIFIED   KENDALL     ANDREW   

       middle_name  res_street_address res_city_desc state_cd  zip_code  \
915380     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915381     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915382     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915383     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915384     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915385     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   
915386     MAXWELL  367  WINFREE RD        WADESBORO       NC   28170.0   

       race_code ethnic_code party_cd gender_code  birth_age birth_state  \
915380         W          NL      UNA           M         26          NC   
915381         W          NL      UNA           M         26          NC   
915382         W          NL      UNA           M         26          NC   
915383         W          NL      UNA           M         26          NC   
915384         W          NL      UNA           M         26          NC   
915385         W          NL      UNA           M         26          NC   
915386         W          NL      UNA           M         26          NC   

       drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
915380           Y  12/28/2011          WADES              9.0   
915381           Y  12/28/2011          WADES              9.0   
915382           Y  12/28/2011          WADES              9.0   
915383           Y  12/28/2011          WADES              9.0   
915384           Y  12/28/2011          WADES              9.0   
915385           Y  12/28/2011          WADES              9.0   
915386           Y  12/28/2011          WADES              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
915380               16A              16A             25.0            55.0   
915381               16A              16A             25.0            55.0   
915382               16A              16A             25.0            55.0   
915383               16A              16A             25.0            55.0   
915384               16

ncid       election_desc  county_id  voter_reg_num election_lbl  \
925113  CW686684  11/03/2020 GENERAL        4.0        35897.0   11/03/2020   
925114  CW686684  11/06/2018 GENERAL        4.0        35897.0   11/06/2018   
925115  CW686684  11/08/2016 GENERAL        4.0        35897.0   11/08/2016   
925116  CW686684  11/04/2014 GENERAL        NaN            NaN          NaN   
925117  CW686684  11/06/2012 GENERAL        4.0        35897.0   11/06/2012   
925118  CW686684  11/06/2012 GENERAL        4.0        35897.0   11/06/2012   
925119  CW686684                None        NaN            NaN          NaN   

       voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
925113     IN-PERSON            REP      BURN              4.0      BURN   
925114     IN-PERSON            REP      BURN              4.0      BURN   
925115     IN-PERSON            REP      BURN              4.0      BURN   
925116           NaN            NaN       NaN              NaN       NaN   
925117   PROVISIONAL            REP      017A             90.0      017A   
925118     IN-PERSON            REP       203             60.0       203   
925119           NaN            NaN       NaN              NaN       NaN   

       voter_status_desc voter_status_reason_desc last_name first_name  \
925113            ACTIVE               UNVERIFIED      LYNN      RENEE   
925114            ACTIVE               UNVERIFIED      LYNN      RENEE   
925115            ACTIVE               UNVERIFIED      LYNN      RENEE   
925116            ACTIVE               UNVERIFIED      LYNN      RENEE   
925117            ACTIVE               UNVERIFIED      LYNN      RENEE   
925118            ACTIVE               UNVERIFIED      LYNN      RENEE   
925119            ACTIVE               UNVERIFIED      LYNN      RENEE   

       middle_name             res_street_address res_city_desc state_cd  \
925113    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925114    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925115    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925116    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925117    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925118    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   
925119    JEANETTE  275  ROCKY RIVER CHURCH RD          POLKTON       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
925113   28135.0         W          NL      REP           F         51   
925114   28135.0         W          NL      REP           F         51   
925115   28135.0         W          NL      REP           F         51   
925116   28135.0         W          NL      REP           F         51   
925117   28135.0         W          NL      REP           F         51   
925118   28135.0         W          NL      REP           F         51   
925119   28135.0         W          NL      REP           F         51   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
925113          NY           Y  07/07/2016           BURN              9.0   
925114          NY           Y  07/07/2016           BURN              9.0   
925115          NY           Y  07/07/2016           BURN              9.0   
925116          NY           Y  07/07/2016           BURN              9.0   
925117          NY           Y  07/07/2016           BURN              9.0   
925118          NY           Y  07/07/2016           BURN              9.0   
925119          NY           Y  07/07/2016           BURN              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
925113               16A              16A             25.0            55.0   
925114               16A              16A             25.0            55.0   
925115               16A              16A             25.0            55.0   
925116               16A              

ncid       election_desc  county_id  voter_reg_num election_lbl  \
950062  AB14598  11/03/2020 GENERAL        NaN            NaN          NaN   
950063  AB14598  11/06/2018 GENERAL        NaN            NaN          NaN   
950064  AB14598  11/08/2016 GENERAL        4.0        32922.0   11/08/2016   
950065  AB14598  11/04/2014 GENERAL        4.0        32922.0   11/04/2014   
950066  AB14598  11/06/2012 GENERAL        4.0        32922.0   11/06/2012   
950067  AB14598  11/06/2012 GENERAL        4.0        32922.0   11/06/2012   
950068  AB14598                None        NaN            NaN          NaN   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
950062               NaN            NaN       NaN              NaN       NaN   
950063               NaN            NaN       NaN              NaN       NaN   
950064         IN-PERSON            DEM      LILE              4.0      LILE   
950065  ABSENTEE ONESTOP            DEM      LILE              4.0      LILE   
950066         IN-PERSON            REP        B2              2.0        B2   
950067  ABSENTEE ONESTOP            DEM      LILE              4.0      LILE   
950068               NaN            NaN       NaN              NaN       NaN   

       voter_status_desc voter_status_reason_desc last_name first_name  \
950062            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950063            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950064            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950065            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950066            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950067            ACTIVE                 VERIFIED     SMITH    ANTHONY   
950068            ACTIVE                 VERIFIED     SMITH    ANTHONY   

       middle_name  res_street_address res_city_desc state_cd  zip_code  \
950062        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950063        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950064        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950065        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950066        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950067        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   
950068        DALE  115 S SECOND ST       LILESVILLE       NC   28091.0   

       race_code ethnic_code party_cd gender_code  birth_age birth_state  \
950062         B          UN      DEM           M         48          NC   
950063         B          UN      DEM           M         48          NC   
950064         B          UN      DEM           M         48          NC   
950065         B          UN      DEM           M         48          NC   
950066         B          UN      DEM           M         48          NC   
950067         B          UN      DEM           M         48          NC   
950068         B          UN      DEM           M         48          NC   

       drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
950062           Y  11/02/2012           LILE              9.0   
950063           Y  11/02/2012           LILE              9.0   
950064           Y  11/02/2012           LILE              9.0   
950065           Y  11/02/2012           LILE              9.0   
950066           Y  11/02/2012           LILE              9.0   
950067           Y  11/02/2012           LILE              9.0   
950068           Y  11/02/2012           LILE              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
950062               16A              16A             25.0            55.0   
950063               16A              16A             25.0            55.0   
950064               16A              16A             25.0            55.0   
950065               16A              16A             25.0            55.0   
950066               16

...

ncid       election_desc  county_id  voter_reg_num election_lbl  \
44013983  EP46816  11/03/2020 GENERAL        NaN            NaN          NaN   
44013984  EP46816  11/06/2018 GENERAL        NaN            NaN          NaN   
44013985  EP46816  11/08/2016 GENERAL       98.0    757513184.0   11/08/2016   
44013986  EP46816  11/04/2014 GENERAL       98.0    757513184.0   11/04/2014   
44013987  EP46816  11/06/2012 GENERAL       98.0    757513184.0   11/06/2012   
44013988  EP46816  11/06/2012 GENERAL       98.0    757513184.0   11/06/2012   
44013989  EP46816                None        NaN            NaN          NaN   

             voting_method voted_party_cd pct_label  voted_county_id  \
44013983               NaN            NaN       NaN              NaN   
44013984               NaN            NaN       NaN              NaN   
44013985         IN-PERSON            REP        16             10.0   
44013986         IN-PERSON            REP        16             10.0   
44013987         IN-PERSON            REP        16             10.0   
44013988  ABSENTEE ONESTOP            DEM      PRGA             98.0   
44013989               NaN            NaN       NaN              NaN   

         vtd_label voter_status_desc voter_status_reason_desc last_name  \
44013983       NaN            ACTIVE                 VERIFIED     ELLIS   
44013984       NaN            ACTIVE                 VERIFIED     ELLIS   
44013985        16            ACTIVE                 VERIFIED     ELLIS   
44013986        16            ACTIVE                 VERIFIED     ELLIS   
44013987        16            ACTIVE                 VERIFIED     ELLIS   
44013988      PRGA            ACTIVE                 VERIFIED     ELLIS   
44013989       NaN            ACTIVE                 VERIFIED     ELLIS   

         first_name middle_name           res_street_address res_city_desc  \
44013983  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013984  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013985  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013986  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013987  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013988  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   
44013989  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A        WILSON   

         state_cd  zip_code race_code ethnic_code party_cd gender_code  \
44013983       NC   27896.0         W          UN      REP           M   
44013984       NC   27896.0         W          UN      REP           M   
44013985       NC   27896.0         W          UN      REP           M   
44013986       NC   27896.0         W          UN      REP           M   
44013987       NC   27896.0         W          UN      REP           M   
44013988       NC   27896.0         W          UN      REP           M   
44013989       NC   27896.0         W          UN      REP           M   

          birth_age birth_state drivers_lic  registr_dt precinct_abbrv  \
44013983         69          NC           Y  01/22/2019           PRTA   
44013984         69          NC           Y  01/22/2019           PRTA   
44013985         69          NC           Y  01/22/2019           PRTA   
44013986         69          NC           Y  01/22/2019           PRTA   
44013987         69          NC           Y  01/22/2019           PRTA   
44013988         69          NC           Y  01/22/2019           PRTA   
44013989         69          NC           Y  01/22/2019           PRTA   

          cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
44013983              1.0               07C               07              4.0   
44013984              1.0               07C               07              4.0   
44013985              1.0               07C               07              4.0   
44013986              1.0               07C               0

ncid       election_desc  county_id  voter_reg_num election_lbl  \
44156622  EP80424  11/03/2020 GENERAL        NaN            NaN          NaN   
44156623  EP80424  11/06/2018 GENERAL       98.0    757480595.0   11/06/2018   
44156624  EP80424  11/08/2016 GENERAL       98.0    757480595.0   11/08/2016   
44156625  EP80424  11/04/2014 GENERAL       98.0    757480595.0   11/04/2014   
44156626  EP80424  11/06/2012 GENERAL       98.0    757480595.0   11/06/2012   
44156627  EP80424  11/06/2012 GENERAL       98.0    757480595.0   11/06/2012   
44156628  EP80424                None        NaN            NaN          NaN   

             voting_method voted_party_cd pct_label  voted_county_id  \
44156622               NaN            NaN       NaN              NaN   
44156623         IN-PERSON            DEM      PRSP             98.0   
44156624         IN-PERSON            DEM      PRSP             98.0   
44156625         IN-PERSON            DEM      PRSP             98.0   
44156626  ABSENTEE ONESTOP            DEM       4-B             70.0   
44156627  ABSENTEE ONESTOP            DEM      PRSP             98.0   
44156628               NaN            NaN       NaN              NaN   

         vtd_label voter_status_desc voter_status_reason_desc last_name  \
44156622       NaN            ACTIVE                 VERIFIED      PITT   
44156623      PRSP            ACTIVE                 VERIFIED      PITT   
44156624      PRSP            ACTIVE                 VERIFIED      PITT   
44156625      PRSP            ACTIVE                 VERIFIED      PITT   
44156626       4-B            ACTIVE                 VERIFIED      PITT   
44156627      PRSP            ACTIVE                 VERIFIED      PITT   
44156628       NaN            ACTIVE                 VERIFIED      PITT   

          first_name middle_name           res_street_address res_city_desc  \
44156622  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156623  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156624  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156625  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156626  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156627  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   
44156628  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD            KENLY   

         state_cd  zip_code race_code ethnic_code party_cd gender_code  \
44156622       NC   27542.0         B          NL      DEM           M   
44156623       NC   27542.0         B          NL      DEM           M   
44156624       NC   27542.0         B          NL      DEM           M   
44156625       NC   27542.0         B          NL      DEM           M   
44156626       NC   27542.0         B          NL      DEM           M   
44156627       NC   27542.0         B          NL      DEM           M   
44156628       NC   27542.0         B          NL      DEM           M   

          birth_age birth_state drivers_lic  registr_dt precinct_abbrv  \
44156622         31          MD           Y  09/30/2008           PRSP   
44156623         31          MD           Y  09/30/2008           PRSP   
44156624         31          MD           Y  09/30/2008           PRSP   
44156625         31          MD           Y  09/30/2008           PRSP   
44156626         31          MD           Y  09/30/2008           PRSP   
44156627         31          MD           Y  09/30/2008           PRSP   
44156628         31          MD           Y  09/30/2008           PRSP   

          cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
44156622              1.0               07C               07              4.0   
44156623              1.0               07C               07              4.0   
44156624              1.0               07C               07              4.0   
44156625              1.0               07C        

ncid       election_desc  county_id  voter_reg_num election_lbl  \
44230471  EP21414  11/03/2020 GENERAL        NaN            NaN          NaN   
44230472  EP21414  11/06/2018 GENERAL       98.0        27375.0   11/06/2018   
44230473  EP21414  11/08/2016 GENERAL       98.0        27375.0   11/08/2016   
44230474  EP21414  11/04/2014 GENERAL       98.0        27375.0   11/04/2014   
44230475  EP21414  11/06/2012 GENERAL       98.0        27375.0   11/06/2012   
44230476  EP21414  11/06/2012 GENERAL       98.0        27375.0   11/06/2012   
44230477  EP21414                None        NaN            NaN          NaN   

             voting_method voted_party_cd pct_label  voted_county_id  \
44230471               NaN            NaN       NaN              NaN   
44230472  ABSENTEE ONESTOP            REP      PRGA             98.0   
44230473  ABSENTEE ONESTOP            REP      PRGA             98.0   
44230474         IN-PERSON            REP      0035             64.0   
44230475  ABSENTEE ONESTOP            DEM      PRCR             98.0   
44230476  ABSENTEE ONESTOP            REP      0035             64.0   
44230477               NaN            NaN       NaN              NaN   

         vtd_label voter_status_desc voter_status_reason_desc last_name  \
44230471       NaN            ACTIVE                 VERIFIED    WATSON   
44230472      PRGA            ACTIVE                 VERIFIED    WATSON   
44230473      PRGA            ACTIVE                 VERIFIED    WATSON   
44230474      0035            ACTIVE                 VERIFIED    WATSON   
44230475      PRCR            ACTIVE                 VERIFIED    WATSON   
44230476      0035            ACTIVE                 VERIFIED    WATSON   
44230477       NaN            ACTIVE                 VERIFIED    WATSON   

         first_name middle_name         res_street_address res_city_desc  \
44230471     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230472     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230473     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230474     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230475     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230476     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   
44230477     BRENDA      BAILEY  4300  US HWY 264 ALT  E          WILSON   

         state_cd  zip_code race_code ethnic_code party_cd gender_code  \
44230471       NC   27893.0         W          NL      REP           F   
44230472       NC   27893.0         W          NL      REP           F   
44230473       NC   27893.0         W          NL      REP           F   
44230474       NC   27893.0         W          NL      REP           F   
44230475       NC   27893.0         W          NL      REP           F   
44230476       NC   27893.0         W          NL      REP           F   
44230477       NC   27893.0         W          NL      REP           F   

          birth_age birth_state drivers_lic  registr_dt precinct_abbrv  \
44230471         71          NC           Y  10/09/1968           PRGA   
44230472         71          NC           Y  10/09/1968           PRGA   
44230473         71          NC           Y  10/09/1968           PRGA   
44230474         71          NC           Y  10/09/1968           PRGA   
44230475         71          NC           Y  10/09/1968           PRGA   
44230476         71          NC           Y  10/09/1968           PRGA   
44230477         71          NC           Y  10/09/1968           PRGA   

          cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
44230471              1.0               07B               07              4.0   
44230472              1.0               07B               07              4.0   
44230473              1.0               07B               07              4.0   
44230474              1.0               07B               07              4

ncid       election_desc  county_id  voter_reg_num election_lbl  \
44292482  ER43863  11/03/2020 GENERAL       99.0        79756.0   11/03/2020   
44292483  ER43863  11/06/2018 GENERAL       99.0        79756.0   11/06/2018   
44292484  ER43863  11/06/2018 GENERAL       99.0        79756.0   11/06/2018   
44292485  ER43863  11/08/2016 GENERAL        NaN            NaN          NaN   
44292486  ER43863  11/04/2014 GENERAL        NaN            NaN          NaN   
44292487  ER43863  11/06/2012 GENERAL        NaN            NaN          NaN   
44292488  ER43863                None        NaN            NaN          NaN   

             voting_method voted_party_cd pct_label  voted_county_id  \
44292482  ABSENTEE ONESTOP            REP      BNVL             99.0   
44292483  ABSENTEE ONESTOP            REP      BNVL             99.0   
44292484  ABSENTEE ONESTOP            REP      1507             74.0   
44292485               NaN            NaN       NaN              NaN   
44292486               NaN            NaN       NaN              NaN   
44292487               NaN            NaN       NaN              NaN   
44292488               NaN            NaN       NaN              NaN   

         vtd_label voter_status_desc voter_status_reason_desc last_name  \
44292482      BNVL            ACTIVE                 VERIFIED     DAVIS   
44292483      BNVL            ACTIVE                 VERIFIED     DAVIS   
44292484      1507            ACTIVE                 VERIFIED     DAVIS   
44292485       NaN            ACTIVE                 VERIFIED     DAVIS   
44292486       NaN            ACTIVE                 VERIFIED     DAVIS   
44292487       NaN            ACTIVE                 VERIFIED     DAVIS   
44292488       NaN            ACTIVE                 VERIFIED     DAVIS   

         first_name middle_name res_street_address res_city_desc state_cd  \
44292482     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292483     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292484     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292485     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292486     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292487     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   
44292488     DENVER       SMITH   1200  MEAD RD        BOONVILLE       NC   

          zip_code race_code ethnic_code party_cd gender_code  birth_age  \
44292482   27011.0         W          NL      REP           M         21   
44292483   27011.0         W          NL      REP           M         21   
44292484   27011.0         W          NL      REP           M         21   
44292485   27011.0         W          NL      REP           M         21   
44292486   27011.0         W          NL      REP           M         21   
44292487   27011.0         W          NL      REP           M         21   
44292488   27011.0         W          NL      REP           M         21   

         birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
44292482          NC           Y  11/02/2018           BNVL             10.0   
44292483          NC           Y  11/02/2018           BNVL             10.0   
44292484          NC           Y  11/02/2018           BNVL             10.0   
44292485          NC           Y  11/02/2018           BNVL             10.0   
44292486          NC           Y  11/02/2018           BNVL             10.0   
44292487          NC           Y  11/02/2018           BNVL             10.0   
44292488          NC           Y  11/02/2018           BNVL             10.0   

         super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
44292482                23               23             34.0            73.0   
44292483                23               23             34.0            73.0   
44292484                23               23             34.0            73.0   
4429248

ncid       election_desc  county_id  voter_reg_num election_lbl  \
44403657  ER15626  11/03/2020 GENERAL       99.0        15048.0   11/03/2020   
44403658  ER15626  11/06/2018 GENERAL       99.0        15048.0   11/06/2018   
44403659  ER15626  11/08/2016 GENERAL       99.0        15048.0   11/08/2016   
44403660  ER15626  11/08/2016 GENERAL       99.0        15048.0   11/08/2016   
44403661  ER15626  11/04/2014 GENERAL       99.0        15048.0   11/04/2014   
44403662  ER15626  11/04/2014 GENERAL       99.0        15048.0   11/04/2014   
44403663  ER15626  11/06/2012 GENERAL       99.0        15048.0   11/06/2012   
44403664  ER15626  11/06/2012 GENERAL       99.0        15048.0   11/06/2012   
44403665  ER15626                None        NaN            NaN          NaN   

             voting_method voted_party_cd pct_label  voted_county_id  \
44403657  ABSENTEE ONESTOP            REP      SFAL             99.0   
44403658  ABSENTEE ONESTOP            REP      SFAL             99.0   
44403659  ABSENTEE ONESTOP            REP       133             34.0   
44403660         IN-PERSON            REP      SFAL             99.0   
44403661         IN-PERSON            REP       133             34.0   
44403662         IN-PERSON            REP      SFAL             99.0   
44403663  ABSENTEE BY MAIL            REP       133             34.0   
44403664  ABSENTEE ONESTOP            REP      SFAL             99.0   
44403665               NaN            NaN       NaN              NaN   

         vtd_label voter_status_desc voter_status_reason_desc last_name  \
44403657      SFAL            ACTIVE                 VERIFIED  WILLIAMS   
44403658      SFAL            ACTIVE                 VERIFIED  WILLIAMS   
44403659       133            ACTIVE                 VERIFIED  WILLIAMS   
44403660      SFAL            ACTIVE                 VERIFIED  WILLIAMS   
44403661       133            ACTIVE                 VERIFIED  WILLIAMS   
44403662      SFAL            ACTIVE                 VERIFIED  WILLIAMS   
44403663       133            ACTIVE                 VERIFIED  WILLIAMS   
44403664      SFAL            ACTIVE                 VERIFIED  WILLIAMS   
44403665       NaN            ACTIVE                 VERIFIED  WILLIAMS   

         first_name middle_name   res_street_address res_city_desc state_cd  \
44403657      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403658      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403659      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403660      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403661      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403662      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403663      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403664      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   
44403665      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND       NC   

          zip_code race_code ethnic_code party_cd gender_code  birth_age  \
44403657   27018.0         W          NL      REP           F         51   
44403658   27018.0         W          NL      REP           F         51   
44403659   27018.0         W          NL      REP           F         51   
44403660   27018.0         W          NL      REP           F         51   
44403661   27018.0         W          NL      REP           F         51   
44403662   27018.0         W          NL      REP           F         51   
44403663   27018.0         W          NL      REP           F         51   
44403664   27018.0         W          NL      REP           F         51   
44403665   27018.0         W          NL      REP           F         51   

         birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
44403657          NC           Y  03/09/1988           SFAL             10.0   
44403658          NC        

> Because several of these ncids have conflicts in more than one election and because it is not possible to verify which records may be correct, these 303 ncids will be dropped from analysis.

In [13]:
#########################################################################
# Drop the following rows to deal with duplicate votes cast by same ncid 
# in same election:
#########################################################################

## Drop all record for all ncids that have duplicates in any major election
voter_elecs.drop(index=voter_elecs.loc[voter_elecs['ncid'].isin(dup_ncid_elecs['ncid'].unique())].index,
                inplace=True)

In [14]:
## Check that all duplicates have been successfully dealt with
voter_elecs.duplicated(subset=['ncid', 'election_desc']).sum()

0

In [15]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_no_dup_ncids.zip', index=False)

## Engineer Features for Grouping and Modeling

In [ ]:
## Load in NC statewide voter history and info by election
# voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_no_dup_ncids.zip',
#                           dtype={'precinct_abbrv': str, 
#                               'super_court_abbrv': str, 
#                               'judic_dist_abbrv': str,
#                               'school_dist_abbrv': str,
#                               'vtd_abbrv': str
#                                 })

In [16]:
voter_elecs.head()

ncid       election_desc  county_id  voter_reg_num election_lbl  \
0  AA56273  11/03/2020 GENERAL        1.0      9005990.0   11/03/2020   
1  AA56273  11/06/2018 GENERAL        1.0      9005990.0   11/06/2018   
2  AA56273  11/08/2016 GENERAL        1.0      9005990.0   11/08/2016   
3  AA56273  11/04/2014 GENERAL        1.0      9005990.0   11/04/2014   
4  AA56273  11/06/2012 GENERAL        1.0      9005990.0   11/06/2012   

      voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
0  ABSENTEE BY MAIL            UNA       08N              1.0       08N   
1         IN-PERSON            UNA       08N              1.0       08N   
2         IN-PERSON            UNA       08N              1.0       08N   
3         IN-PERSON            UNA       08N              1.0       08N   
4         IN-PERSON            UNA       08N              1.0       08N   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
1            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
2            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
3            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
4            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   

                    res_street_address res_city_desc state_cd  zip_code  \
0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
1  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
2  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
3  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
4  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   

  race_code ethnic_code party_cd gender_code  birth_age birth_state  \
0         W          NL      UNA           F         85          NY   
1         W          NL      UNA           F         85          NY   
2         W          NL      UNA           F         85          NY   
3         W          NL      UNA           F         85          NY   
4         W          NL      UNA           F         85          NY   

  drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0           N  10/01/1984            08N             13.0               15A   
1           N  10/01/1984            08N             13.0               15A   
2           N  10/01/1984            08N             13.0               15A   
3           N  10/01/1984            08N             13.0               15A   
4           N  10/01/1984            08N             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv  
0          17.0                N        1935       08N  
1          17.0                N        1935       08N  
2          17.0                N        1935       08N  
3          17.0                N        1935       08N  
4          17.0                N        1935       08N

In [17]:
## Recast election_lbl as datetime
voter_elecs['election_lbl'] = pd.to_datetime(
    voter_elecs['election_desc'].str.split(' ',
                                           n=1).apply(
        # Where election_desc is 'None' fill with NaN
        lambda x: x[0]).replace({'None':np.nan}))

# ## Create a new col for just the year
# voter_elecs.insert(loc=5, column='election_yr',
#                  value=voter_elecs['election_lbl'].dt.year)

In [18]:
## Create a binary variable indicating whether or not in individual registered
  ## in time to vote in that election

# Calculate normal registration deadline for the election
  # (25 days before election in NC, but afterwards have option to register 
  #  in person during early voting period)
voter_elecs.insert(loc=5, column='registr_deadline',
                 value=pd.to_datetime(voter_elecs['election_lbl'] - dt.timedelta(days=25)))

# Recast voter registration date as datetime variable 
voter_elecs['registr_dt'] = pd.to_datetime(voter_elecs['registr_dt'])

# Check whether or not an individual voted (if they did, they were registered
  # in time and may have registered in person after the normal deadline) and
  # compare registration date to registration deadline
voter_elecs.insert(loc=6, column='registr_in_time',
                 value=np.where(((voter_elecs['voting_method'].isna()) & 
                                 (voter_elecs['registr_dt'] > voter_elecs['registr_deadline'])),
                                0,1))

In [19]:
## Drop registr_deadline column
voter_elecs.drop(columns=['registr_deadline'], inplace=True)

In [20]:
## Create a column for age adjusted according to the specific election year
voter_elecs.insert(loc=6, column='birth_age_adj',
                   value=voter_elecs['election_lbl'].dt.year.subtract(voter_elecs['birth_year']))

In [22]:
## Group original vote methods into more general categories in a new variable
 # Map the original categoriess to new ones
vote_method_map = {'ABSENTEE ONESTOP': 'Early',
                   'IN-PERSON': 'Election Day',
                   'ABSENTEE BY MAIL': 'Early',
                   'ABSENTEE CURBSIDE': 'Early',
                   'TRANSFER': 'Other',
                   'PROVISIONAL': 'Other',
                   'CURBSIDE': 'Election Day'}

# Apply the map to create new vote_method_cat column
voter_elecs.insert(loc=8, column='vote_method_cat',
                 value=voter_elecs['voting_method'].map(vote_method_map))

In [23]:
## Inspect updated df
voter_elecs.head(35)

ncid       election_desc  county_id  voter_reg_num election_lbl  \
0    AA56273  11/03/2020 GENERAL        1.0      9005990.0   2020-11-03   
1    AA56273  11/06/2018 GENERAL        1.0      9005990.0   2018-11-06   
2    AA56273  11/08/2016 GENERAL        1.0      9005990.0   2016-11-08   
3    AA56273  11/04/2014 GENERAL        1.0      9005990.0   2014-11-04   
4    AA56273  11/06/2012 GENERAL        1.0      9005990.0   2012-11-06   
5    AA56273                None        NaN            NaN          NaT   
6   AA201627  11/03/2020 GENERAL        1.0      9178574.0   2020-11-03   
7   AA201627  11/06/2018 GENERAL        NaN            NaN   2018-11-06   
8   AA201627  11/08/2016 GENERAL        NaN            NaN   2016-11-08   
9   AA201627  11/04/2014 GENERAL        NaN            NaN   2014-11-04   
10  AA201627  11/06/2012 GENERAL        NaN            NaN   2012-11-06   
11  AA201627                None        NaN            NaN          NaT   
12  AA216996  11/03/2020 GENERAL        1.0      9205561.0   2020-11-03   
13  AA216996  11/06/2018 GENERAL        NaN            NaN   2018-11-06   
14  AA216996  11/08/2016 GENERAL        NaN            NaN   2016-11-08   
15  AA216996  11/04/2014 GENERAL        NaN            NaN   2014-11-04   
16  AA216996  11/06/2012 GENERAL        NaN            NaN   2012-11-06   
17  AA216996                None        NaN            NaN          NaT   
18   AA98377  11/03/2020 GENERAL        1.0      9048723.0   2020-11-03   
19   AA98377  11/06/2018 GENERAL        1.0      9048723.0   2018-11-06   
20   AA98377  11/08/2016 GENERAL        1.0      9048723.0   2016-11-08   
21   AA98377  11/04/2014 GENERAL        1.0      9048723.0   2014-11-04   
22   AA98377  11/06/2012 GENERAL        1.0      9048723.0   2012-11-06   
23   AA98377                None        NaN            NaN          NaT   
24   AA69747  11/03/2020 GENERAL        1.0      9019674.0   2020-11-03   
25   AA69747  11/06/2018 GENERAL        1.0      9019674.0   2018-11-06   
26   AA69747  11/08/2016 GENERAL        1.0      9019674.0   2016-11-08   
27   AA69747  11/04/2014 GENERAL        1.0      9019674.0   2014-11-04   
28   AA69747  11/06/2012 GENERAL        1.0      9019674.0   2012-11-06   
29   AA69747                None        NaN            NaN          NaT   
30  AA170513  11/03/2020 GENERAL        1.0      9129589.0   2020-11-03   
31  AA170513  11/06/2018 GENERAL        1.0      9129589.0   2018-11-06   
32  AA170513  11/08/2016 GENERAL        1.0      9129589.0   2016-11-08   
33  AA170513  11/04/2014 GENERAL        1.0      9129589.0   2014-11-04   
34  AA170513  11/06/2012 GENERAL        1.0      9129589.0   2012-11-06   

    registr_in_time  birth_age_adj     voting_method vote_method_cat  \
0                 1           85.0  ABSENTEE BY MAIL           Early   
1                 1           83.0         IN-PERSON    Election Day   
2                 1           81.0         IN-PERSON    Election Day   
3                 1           79.0         IN-PERSON    Election Day   
4                 1           77.0         IN-PERSON    Election Day   
5                 1            NaN               NaN             NaN   
6                 1           42.0  ABSENTEE ONESTOP           Early   
7                 1           40.0               NaN             NaN   
8                 0           38.0               NaN             NaN   
9                 0           36.0               NaN             NaN   
10                0           34.0               NaN             NaN   
11                1            NaN               NaN             NaN   
12                1           54.0  ABSENTEE ONESTOP           Early   
13                0           52.0               NaN             NaN   
14                0           50.0               NaN             NaN   
15                0           48.0               NaN             NaN   
16                0           46.0               NaN             NaN   
17         

In [24]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

## Create a DataFrame Summarizing Each Voter's History

In [ ]:
## Aggregate individual ncid's to find a way to easily identify individuals
  ## with no recent voting history
ncid_grp_sum = voter_elecs.groupby('ncid').sum().reset_index()
ncid_grp_sum.head(20)

In [ ]:
## Inspect record for an individual with no recent voting history
ncid_grp_sum.loc[ncid_grp_sum['ncid']=='AL261840']
## voter_reg_num shows up as 0 when an individual has no voting history

In [ ]:
## 990,485 voters currently registered in NC have not voted in a 
## major election so far
never_voted_maj_elec = ncid_grp_sum.loc[ncid_grp_sum['voter_reg_num']==0][['ncid']]
len(never_voted_maj_elec)

In [28]:
## Insert a binary column indicating that a voter has no history for voting
  ## in recent major elections (1) or has recently voted at least once (0)
voter_elecs.insert(loc=2, column='no_vote_his',
                 value=np.where(voter_elecs['ncid'].isin(never_voted_maj_elec['ncid']),
                               1,0))

In [ ]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

In [29]:
## Set multiindex for df grouping first by ncid, then election_desc
voter_elecs_mi = voter_elecs.set_index(['ncid','election_desc'])
voter_elecs_mi.head()

no_vote_his  county_id  voter_reg_num  \
ncid    election_desc                                               
AA56273 11/03/2020 GENERAL            0        1.0      9005990.0   
        11/06/2018 GENERAL            0        1.0      9005990.0   
        11/08/2016 GENERAL            0        1.0      9005990.0   
        11/04/2014 GENERAL            0        1.0      9005990.0   
        11/06/2012 GENERAL            0        1.0      9005990.0   

                           election_lbl  registr_in_time  birth_age_adj  \
ncid    election_desc                                                     
AA56273 11/03/2020 GENERAL   2020-11-03                1           85.0   
        11/06/2018 GENERAL   2018-11-06                1           83.0   
        11/08/2016 GENERAL   2016-11-08                1           81.0   
        11/04/2014 GENERAL   2014-11-04                1           79.0   
        11/06/2012 GENERAL   2012-11-06                1           77.0   

                               voting_method vote_method_cat voted_party_cd  \
ncid    election_desc                                                         
AA56273 11/03/2020 GENERAL  ABSENTEE BY MAIL           Early            UNA   
        11/06/2018 GENERAL         IN-PERSON    Election Day            UNA   
        11/08/2016 GENERAL         IN-PERSON    Election Day            UNA   
        11/04/2014 GENERAL         IN-PERSON    Election Day            UNA   
        11/06/2012 GENERAL         IN-PERSON    Election Day            UNA   

                           pct_label  voted_county_id vtd_label  \
ncid    election_desc                                             
AA56273 11/03/2020 GENERAL       08N              1.0       08N   
        11/06/2018 GENERAL       08N              1.0       08N   
        11/08/2016 GENERAL       08N              1.0       08N   
        11/04/2014 GENERAL       08N              1.0       08N   
        11/06/2012 GENERAL       08N              1.0       08N   

                           voter_status_desc voter_status_reason_desc  \
ncid    election_desc                                                   
AA56273 11/03/2020 GENERAL            ACTIVE                 VERIFIED   
        11/06/2018 GENERAL            ACTIVE                 VERIFIED   
        11/08/2016 GENERAL            ACTIVE                 VERIFIED   
        11/04/2014 GENERAL            ACTIVE                 VERIFIED   
        11/06/2012 GENERAL            ACTIVE                 VERIFIED   

                           last_name first_name middle_name  \
ncid    election_desc                                         
AA56273 11/03/2020 GENERAL     AABEL       RUTH      EVELYN   
        11/06/2018 GENERAL     AABEL       RUTH      EVELYN   
        11/08/2016 GENERAL     AABEL       RUTH      EVELYN   
        11/04/2014 GENERAL     AABEL       RUTH      EVELYN   
        11/06/2012 GENERAL     AABEL       RUTH      EVELYN   

                                             res_street_address res_city_desc  \
ncid    election_desc                                                           
AA56273 11/03/2020 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/06/2018 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/08/2016 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/04/2014 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/06/2012 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   

                           state_cd  zip_code race_code ethnic_code party_cd  \
ncid    election_desc                                                          
AA56273 11/03/2020 GENERAL       NC   27253.0         W          NL      UNA   
        11/06/2018 GENERAL       NC   27253.0         W          NL      UNA   
        11/08/2016 GENERAL       NC   27253.0         W          NL      UNA   
        11/04/2014 GENERAL       NC   27253.0         W          NL     

In [30]:
## Create a dataframe indexed by ncid that records whether and how a person
  ## voted in each major election
voter_elecs_slice = voter_elecs_mi['vote_method_cat'].copy()
maj_elec_methods = voter_elecs_slice.unstack().drop(columns='None')

# Reorder columns
maj_elec_methods = maj_elec_methods[['11/03/2020 GENERAL',
                                     '11/06/2018 GENERAL',
                                     '11/08/2016 GENERAL',
                                     '11/04/2014 GENERAL',
                                     '11/06/2012 GENERAL']]
# Rename columns
maj_elec_methods.columns = ['Gen_2020', 
                            'Gen_2018', 
                            'Gen_2016',
                            'Gen_2014', 
                            'Gen_2012']

# Null values indicate the person did not cast a vote for the election, so
  # make 'No Vote' its own category
maj_elec_methods.fillna('No Vote', inplace=True)

# Inspect df
maj_elec_methods

Gen_2020      Gen_2018 Gen_2016      Gen_2014      Gen_2012
ncid                                                                     
AA100000         Early       No Vote    Early       No Vote       No Vote
AA100004       No Vote       No Vote  No Vote       No Vote       No Vote
AA100006         Early  Election Day    Early  Election Day         Early
AA100007         Early         Early    Early         Early         Early
AA100008       No Vote       No Vote  No Vote       No Vote  Election Day
...                ...           ...      ...           ...           ...
ES9989           Early  Election Day    Early         Early       No Vote
ES9991    Election Day       No Vote  No Vote  Election Day  Election Day
ES9992           Early         Early    Early         Early         Early
ES9997           Early         Early    Early         Early         Early
ES9999           Early         Early    Early         Early         Early

[7415235 rows x 5 columns]

In [31]:
## Check length of df prior to merging with maj_elec_methods
len(voter_elecs)

44491410

In [32]:
## Merge voter_elecs df with maj_elecs_methods according to ncid
voter_elecs = voter_elecs.merge(maj_elec_methods, how='left',
                                   on='ncid')
# Inspect updated df
print(len(voter_elecs)) # length did not change
voter_elecs.head()

44491410


ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0  AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1  AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2  AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3  AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4  AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   

  election_lbl  registr_in_time  birth_age_adj     voting_method  \
0   2020-11-03                1           85.0  ABSENTEE BY MAIL   
1   2018-11-06                1           83.0         IN-PERSON   
2   2016-11-08                1           81.0         IN-PERSON   
3   2014-11-04                1           79.0         IN-PERSON   
4   2012-11-06                1           77.0         IN-PERSON   

  vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0           Early            UNA       08N              1.0       08N   
1    Election Day            UNA       08N              1.0       08N   
2    Election Day            UNA       08N              1.0       08N   
3    Election Day            UNA       08N              1.0       08N   
4    Election Day            UNA       08N              1.0       08N   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
1            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
2            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
3            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
4            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   

                    res_street_address res_city_desc state_cd  zip_code  \
0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
1  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
2  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
3  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
4  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   

  race_code ethnic_code party_cd gender_code  birth_age birth_state  \
0         W          NL      UNA           F         85          NY   
1         W          NL      UNA           F         85          NY   
2         W          NL      UNA           F         85          NY   
3         W          NL      UNA           F         85          NY   
4         W          NL      UNA           F         85          NY   

  drivers_lic registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0           N 1984-10-01            08N             13.0               15A   
1           N 1984-10-01            08N             13.0               15A   
2           N 1984-10-01            08N             13.0               15A   
3           N 1984-10-01            08N             13.0               15A   
4           N 1984-10-01            08N             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv Gen_2020      Gen_2018  \
0          17.0                N        1935       08N    Early  Election Day   
1          17.0                N        1935       08N    Early  Election Day   
2          17.0                N        1935       08N    Early  Election Day   
3          17.0                N        1935       08N    Early  Election Day   
4          17.0                N        1

In [33]:
voter_elecs.head(35)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   
25   AA69747  11/06/2018 GENERAL            0        1.0      9019674.0   
26   AA69747  11/08/2016 GENERAL            0        1.0      9019674.0   
27   AA69747  11/04/2014 GENERAL            0        1.0      9019674.0   
28   AA69747  11/06/2012 GENERAL            0        1.0      9019674.0   
29   AA69747                None            0        NaN            NaN   
30  AA170513  11/03/2020 GENERAL            0        1.0      9129589.0   
31  AA170513  11/06/2018 GENERAL            0        1.0      9129589.0   
32  AA170513  11/08/2016 GENERAL            0        1.0      9129589.0   
33  AA170513  11/04/2014 GENERAL            0        1.0      9129589.0   
34  AA170513  11/06/2012 GENERAL            0        1.0      9129589.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN

In [34]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

In [35]:
voter_elecs.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 44491410 entries, 0 to 44491409
Data columns (total 47 columns):
 #   Column                    Non-Null Count     Dtype         
---  ------                    --------------     -----         
 0   ncid                      44491410 non-null  object        
 1   election_desc             44491410 non-null  object        
 2   no_vote_his               44491410 non-null  int64         
 3   county_id                 20092689 non-null  float64       
 4   voter_reg_num             20092689 non-null  float64       
 5   election_lbl              37076175 non-null  datetime64[ns]
 6   registr_in_time           44491410 non-null  int64         
 7   birth_age_adj             37076175 non-null  float64       
 8   voting_method             20092689 non-null  object        
 9   vote_method_cat           20092665 non-null  object        
 10  voted_party_cd            20084403 non-null  object        
 11  pct_label                 20092689 

In [5]:
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_final.zip',
                          dtype={'precinct_abbrv': str, 
                              'super_court_abbrv': str, 
                              'judic_dist_abbrv': str,
                              'school_dist_abbrv': str,
                              'vtd_abbrv': str
                                })

voter_elecs['election_lbl'] = pd.to_datetime(voter_elecs['election_lbl'])
voter_elecs.head()

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0  AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1  AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2  AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3  AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4  AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   

  election_lbl  registr_in_time  birth_age_adj     voting_method  \
0   2020-11-03                1           85.0  ABSENTEE BY MAIL   
1   2018-11-06                1           83.0         IN-PERSON   
2   2016-11-08                1           81.0         IN-PERSON   
3   2014-11-04                1           79.0         IN-PERSON   
4   2012-11-06                1           77.0         IN-PERSON   

  vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0           Early            UNA       08N              1.0       08N   
1    Election Day            UNA       08N              1.0       08N   
2    Election Day            UNA       08N              1.0       08N   
3    Election Day            UNA       08N              1.0       08N   
4    Election Day            UNA       08N              1.0       08N   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
1            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
2            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
3            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
4            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   

                    res_street_address res_city_desc state_cd  zip_code  \
0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
1  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
2  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
3  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
4  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   

  race_code ethnic_code party_cd gender_code  birth_age birth_state  \
0         W          NL      UNA           F         85          NY   
1         W          NL      UNA           F         85          NY   
2         W          NL      UNA           F         85          NY   
3         W          NL      UNA           F         85          NY   
4         W          NL      UNA           F         85          NY   

  drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0           N  1984-10-01            08N             13.0               15A   
1           N  1984-10-01            08N             13.0               15A   
2           N  1984-10-01            08N             13.0               15A   
3           N  1984-10-01            08N             13.0               15A   
4           N  1984-10-01            08N             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv Gen_2020      Gen_2018  \
0          17.0                N        1935       08N    Early  Election Day   
1          17.0                N        1935       08N    Early  Election Day   
2          17.0                N        1935       08N    Early  Election Day   
3          17.0                N        1935       08N    Early  Election Day   
4          17.0                N   

In [11]:
voter_elecs.head(35)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   
25   AA69747  11/06/2018 GENERAL            0        1.0      9019674.0   
26   AA69747  11/08/2016 GENERAL            0        1.0      9019674.0   
27   AA69747  11/04/2014 GENERAL            0        1.0      9019674.0   
28   AA69747  11/06/2012 GENERAL            0        1.0      9019674.0   
29   AA69747                None            0        NaN            NaN   
30  AA170513  11/03/2020 GENERAL            0        1.0      9129589.0   
31  AA170513  11/06/2018 GENERAL            0        1.0      9129589.0   
32  AA170513  11/08/2016 GENERAL            0        1.0      9129589.0   
33  AA170513  11/04/2014 GENERAL            0        1.0      9129589.0   
34  AA170513  11/06/2012 GENERAL            0        1.0      9129589.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN

In [12]:
## Create a df that summarizes the information known for each ncid
  ## (one record for each ncid)
ncid_summary = voter_elecs.copy()

# Reorder and only include certain columns
ncid_summary = ncid_summary[['ncid', 'no_vote_his', 'voter_status_desc',
                             'voter_status_reason_desc', 'last_name', 
                             'first_name', 'middle_name','party_cd', 
                             'gender_code', 'birth_age', 'birth_year',
                             'registr_dt', 'race_code','ethnic_code', 
                             'zip_code', 'res_street_address',
                             'res_city_desc', 'state_cd', 'birth_state', 
                             'drivers_lic', 'precinct_abbrv',
                             'vtd_abbrv', 'cong_dist_abbrv', 
                             'super_court_abbrv', 'judic_dist_abbrv', 
                             'nc_senate_abbrv', 'nc_house_abbrv', 
                             'school_dist_abbrv', 'Gen_2020', 'Gen_2018',
                             'Gen_2016', 'Gen_2014', 'Gen_2012'   
                            ]]
# With columns that make a record specific to a single election excluded,
  # each row corresponding to a unique ncid should be identical to the others. 
  # Thus, only one row per unique ncid is needed now, drop duplicates
ncid_summary.drop_duplicates(inplace=True)

# Inspect new df
ncid_summary.head()

ncid  no_vote_his voter_status_desc voter_status_reason_desc  \
0    AA56273            0            ACTIVE                 VERIFIED   
6   AA201627            0            ACTIVE                 VERIFIED   
12  AA216996            0            ACTIVE     VERIFICATION PENDING   
18   AA98377            0            ACTIVE                 VERIFIED   
24   AA69747            0            ACTIVE                 VERIFIED   

     last_name first_name middle_name party_cd gender_code  birth_age  \
0        AABEL       RUTH      EVELYN      UNA           F         85   
6       AARDEN       JONI      AUTUMN      UNA           F         42   
12  AARMSTRONG    TIMOTHY       DUANE      REP           M         54   
18       AARON  CHRISTINA    CASTAGNA      UNA           F         44   
24       AARON    CLAUDIA      HAYDEN      UNA           F         75   

    birth_year  registr_dt race_code ethnic_code  zip_code  \
0         1935  1984-10-01         W          NL   27253.0   
6         1978  2018-02-23         W          UN   27302.0   
12        1966  2020-10-31         W          UN   27302.0   
18        1976  1996-03-26         W          UN   27215.0   
24        1945  1989-08-15         W          NL   27215.0   

                     res_street_address res_city_desc state_cd birth_state  \
0   4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC          NY   
6                      117 W CLAY ST           MEBANE       NC          DC   
12               3670  COVINGTON TRL           MEBANE       NC          AL   
18                    421  WHITT AVE       BURLINGTON       NC          NC   
24                    1013  EDITH ST       BURLINGTON       NC          VA   

   drivers_lic precinct_abbrv vtd_abbrv  cong_dist_abbrv super_court_abbrv  \
0            N            08N       08N             13.0               15A   
6            Y            10N       10N             13.0               15A   
12           N            103       103             13.0               15A   
18           Y            03S       03S             13.0               15A   
24           Y            124       124             13.0               15A   

   judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0               15A             24.0            64.0               NaN   
6               15A             24.0            63.0               NaN   
12              15A             24.0            63.0               NaN   
18              15A             24.0            64.0               NaN   
24              15A             24.0            63.0               NaN   

   Gen_2020      Gen_2018      Gen_2016      Gen_2014      Gen_2012  
0     Early  Election Day  Election Day  Election Day  Election Day  
6     Early       No Vote       No Vote       No Vote       No Vote  
12    Early       No Vote       No Vote       No Vote       No Vote  
18    Early  Election Day         Early         Early         Early  
24    Early         Early         Early  Election Day         Early

In [13]:
## Check length of new df and number of unique ncid's to ensure each 
  ## appears only once
print(len(ncid_summary))
ncid_summary['ncid'].nunique()

7415235


7415235

In [8]:
## Check metadata for new summary df
ncid_summary.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14463167 entries, 0 to 44491404
Data columns (total 35 columns):
 #   Column                    Non-Null Count     Dtype  
---  ------                    --------------     -----  
 0   ncid                      14463167 non-null  object 
 1   no_vote_his               14463167 non-null  int64  
 2   voter_status_desc         14463167 non-null  object 
 3   voter_status_reason_desc  14463165 non-null  object 
 4   last_name                 14462847 non-null  object 
 5   first_name                14462980 non-null  object 
 6   middle_name               13481941 non-null  object 
 7   party_cd                  14463167 non-null  object 
 8   gender_code               14463167 non-null  object 
 9   birth_age                 14463167 non-null  int64  
 10  birth_year                14463167 non-null  int64  
 11  registr_dt                14463167 non-null  object 
 12  race_code                 14463167 non-null  object 
 13  ethnic_cod

In [40]:
# ncid_summary.to_csv('Data/NC_ncid_summary.zip', index=False)

## Create Separate DataFrames for Each Election

In [4]:
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_final.zip',
                          dtype={'precinct_abbrv': str, 
                              'super_court_abbrv': str, 
                              'judic_dist_abbrv': str,
                              'school_dist_abbrv': str,
                              'vtd_abbrv': str
                                })

voter_elecs['election_lbl'] = pd.to_datetime(voter_elecs['election_lbl'])

In [5]:
voter_elecs.head(25)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN   
18   2020-11-03                1           44.0  ABSENTEE ONESTOP   
19   2018-11-06                1           42.0         IN-PERSON   
20   2016-11-08                1           40.0  ABSENTEE ONESTOP   
21   2014-11-04                1           38.0  ABSENTEE ONESTOP   
22   2012-11-06                1           36.0  ABSENTEE ONESTOP   
23          NaT                1            NaN               NaN   
24   2020-11-03                1           75.0  ABSENTEE ONESTOP   

   vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0            Early            UNA       08N              1.0       08N   
1     Election Day            UNA       08N              1.0       08N   
2     Election Day            UNA       

In [6]:
## Define function to automate assembling election specific dataframes
def get_election_df(yr):
    
    # Copy original df
    df = voter_elecs.copy()

    # Filter to get only the rows specific to the desired election
    df = df.loc[df['election_lbl'].dt.year==yr]

    # Only keep those voters who registered in time
    df = df.loc[df['registr_in_time']==1]
    
    # Only keep those voters who were old enough to vote in the election
      # (apparently some registration date info is incorrect)
    df = df.loc[df['birth_age_adj']>=18]

    # Reorder and drop certain columns
    df = df[['ncid', 'no_vote_his', 'birth_age_adj', 'voting_method', 
             'Gen_{}'.format(yr), 'party_cd', 'gender_code', 'birth_year', 
             'registr_dt', 'race_code', 'ethnic_code', 'zip_code', 
             'res_street_address', 'res_city_desc', 'state_cd', 'birth_state',
             'drivers_lic', 'county_id', 'voted_county_id', 'precinct_abbrv',
             'vtd_abbrv', 'cong_dist_abbrv', 'super_court_abbrv', 
             'judic_dist_abbrv', 'nc_senate_abbrv', 'nc_house_abbrv',
             'school_dist_abbrv'
            ]]
    
    return df

### General 2020

In [17]:
## Make dataframe specific to 2020 general election
gen_2020 = get_election_df(2020)
print(len(gen_2020))
display(gen_2020.head())
gen_2020.tail()

7347946


ncid  no_vote_his  birth_age_adj     voting_method Gen_2020 party_cd  \
0    AA56273            0           85.0  ABSENTEE BY MAIL    Early      UNA   
6   AA201627            0           42.0  ABSENTEE ONESTOP    Early      UNA   
12  AA216996            0           54.0  ABSENTEE ONESTOP    Early      REP   
18   AA98377            0           44.0  ABSENTEE ONESTOP    Early      UNA   
24   AA69747            0           75.0  ABSENTEE ONESTOP    Early      UNA   

   gender_code  birth_year  registr_dt race_code ethnic_code  zip_code  \
0            F        1935  1984-10-01         W          NL   27253.0   
6            F        1978  2018-02-23         W          UN   27302.0   
12           M        1966  2020-10-31         W          UN   27302.0   
18           F        1976  1996-03-26         W          UN   27215.0   
24           F        1945  1989-08-15         W          NL   27215.0   

                     res_street_address res_city_desc state_cd birth_state  \
0   4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC          NY   
6                      117 W CLAY ST           MEBANE       NC          DC   
12               3670  COVINGTON TRL           MEBANE       NC          AL   
18                    421  WHITT AVE       BURLINGTON       NC          NC   
24                    1013  EDITH ST       BURLINGTON       NC          VA   

   drivers_lic  county_id  voted_county_id precinct_abbrv vtd_abbrv  \
0            N        1.0              1.0            08N       08N   
6            Y        1.0              1.0            10N       10N   
12           N        1.0              1.0            103       103   
18           Y        1.0              1.0            03S       03S   
24           Y        1.0              1.0            124       124   

    cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
0              13.0               15A              15A             24.0   
6              13.0               15A              15A             24.0   
12             13.0               15A              15A             24.0   
18             13.0               15A              15A             24.0   
24             13.0               15A              15A             24.0   

    nc_house_abbrv school_dist_abbrv  
0             64.0               NaN  
6             63.0               NaN  
12            63.0               NaN  
18            64.0               NaN  
24            63.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method Gen_2020  \
44491380  ES17204            0           54.0  ABSENTEE ONESTOP    Early   
44491386  ES26341            0           57.0  ABSENTEE ONESTOP    Early   
44491392  ES26380            0           65.0  ABSENTEE BY MAIL    Early   
44491398  ES28936            1           36.0               NaN  No Vote   
44491404  ES27200            1           56.0               NaN  No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491380      UNA           F        1966  2000-06-01         W          NL   
44491386      REP           F        1963  2015-11-30         W          NL   
44491392      UNA           F        1955  2015-12-18         W          NL   
44491398      UNA           U        1984  2020-06-09         U          UN   
44491404      REP           F        1964  2016-12-29         W          NL   

          zip_code            res_street_address   res_city_desc state_cd  \
44491380   28714.0       2156  LICKSKILLET RD         BURNSVILLE       NC   
44491386   28714.0       250  LAUREL ACRES RD         BURNSVILLE       NC   
44491392   28714.0  91 W BURNSVILLE CHURCH RD         BURNSVILLE       NC   
44491398   28740.0            225  GARLAND LN     GREEN MOUNTAIN       NC   
44491404   28714.0  115  STONEY FALLS LOOP   #D3      BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491380          FL           Y      100.0            100.0         02 CAN   
44491386          CO           Y      100.0            100.0         08 CRA   
44491392          NC           Y      100.0            100.0         01 BUR   
44491398         NaN           Y        NaN              NaN         05 GRE   
44491404          IN           Y        NaN              NaN         11 PRI   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491380    02-CAN             11.0                24               24   
44491386    08-CRA             11.0                24               24   
44491392    01-BUR             11.0                24               24   
44491398    05-GRE             11.0                24               24   
44491404    11-PRI             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491380             47.0           118.0               NaN  
44491386             47.0           118.0               NaN  
44491392             47.0           118.0               NaN  
44491398             47.0           118.0               NaN  
44491404             47.0           118.0               NaN

In [18]:
# gen_2020.to_csv('Data/NC_gen_2020.zip', index=False)

### General 2018

In [19]:
## Make dataframe specific to 2018 general election
gen_2018 = get_election_df(2018)
print(len(gen_2018))
display(gen_2018.head())
gen_2018.tail()

6050078


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2018  \
1    AA56273            0           83.0         IN-PERSON  Election Day   
7   AA201627            0           40.0               NaN       No Vote   
19   AA98377            0           42.0         IN-PERSON  Election Day   
25   AA69747            0           73.0  ABSENTEE ONESTOP         Early   
31  AA170513            0           70.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
1       UNA           F        1935  1984-10-01         W          NL   
7       UNA           F        1978  2018-02-23         W          UN   
19      UNA           F        1976  1996-03-26         W          UN   
25      UNA           F        1945  1989-08-15         W          NL   
31      DEM           M        1948  2012-03-07         W          UN   

    zip_code                   res_street_address res_city_desc state_cd  \
1    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
7    27302.0                     117 W CLAY ST           MEBANE       NC   
19   27215.0                    421  WHITT AVE       BURLINGTON       NC   
25   27215.0                    1013  EDITH ST       BURLINGTON       NC   
31   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
1           NY           N        1.0              1.0            08N   
7           DC           Y        NaN              NaN            10N   
19          NC           Y        1.0              1.0            03S   
25          VA           Y        1.0              1.0            124   
31          MA           N        1.0              1.0            08N   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
1        08N             13.0               15A              15A   
7        10N             13.0               15A              15A   
19       03S             13.0               15A              15A   
25       124             13.0               15A              15A   
31       08N             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
1              24.0            64.0               NaN  
7              24.0            63.0               NaN  
19             24.0            64.0               NaN  
25             24.0            63.0               NaN  
31             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method Gen_2018  \
44491375  ES26387            0           20.0  ABSENTEE BY MAIL    Early   
44491381  ES17204            0           52.0  ABSENTEE ONESTOP    Early   
44491387  ES26341            0           55.0  ABSENTEE ONESTOP    Early   
44491393  ES26380            0           63.0               NaN  No Vote   
44491405  ES27200            1           54.0               NaN  No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491375      UNA           F        1998  2015-12-31         W          NL   
44491381      UNA           F        1966  2000-06-01         W          NL   
44491387      REP           F        1963  2015-11-30         W          NL   
44491393      UNA           F        1955  2015-12-18         W          NL   
44491405      REP           F        1964  2016-12-29         W          NL   

          zip_code            res_street_address res_city_desc state_cd  \
44491375   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491381   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491387   28714.0       250  LAUREL ACRES RD       BURNSVILLE       NC   
44491393   28714.0  91 W BURNSVILLE CHURCH RD       BURNSVILLE       NC   
44491405   28714.0  115  STONEY FALLS LOOP   #D3    BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491375          NC           Y      100.0            100.0         02 CAN   
44491381          FL           Y      100.0            100.0         02 CAN   
44491387          CO           Y      100.0            100.0         08 CRA   
44491393          NC           Y        NaN              NaN         01 BUR   
44491405          IN           Y        NaN              NaN         11 PRI   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491375    02-CAN             11.0                24               24   
44491381    02-CAN             11.0                24               24   
44491387    08-CRA             11.0                24               24   
44491393    01-BUR             11.0                24               24   
44491405    11-PRI             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491375             47.0           118.0               NaN  
44491381             47.0           118.0               NaN  
44491387             47.0           118.0               NaN  
44491393             47.0           118.0               NaN  
44491405             47.0           118.0               NaN

In [20]:
# gen_2018.to_csv('Data/NC_gen_2018.zip', index=False)

### General 2016

In [21]:
## Make dataframe specific to 2016 general election
gen_2016 = get_election_df(2016)
print(len(gen_2016))
display(gen_2016.head())
gen_2016.tail()

5516340


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2016  \
2    AA56273            0           81.0         IN-PERSON  Election Day   
20   AA98377            0           40.0  ABSENTEE ONESTOP         Early   
26   AA69747            0           71.0  ABSENTEE ONESTOP         Early   
32  AA170513            0           68.0  ABSENTEE ONESTOP         Early   
38   BM49306            0           50.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
2       UNA           F        1935  1984-10-01         W          NL   
20      UNA           F        1976  1996-03-26         W          UN   
26      UNA           F        1945  1989-08-15         W          NL   
32      DEM           M        1948  2012-03-07         W          UN   
38      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
2    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
20   27215.0                    421  WHITT AVE       BURLINGTON       NC   
26   27215.0                    1013  EDITH ST       BURLINGTON       NC   
32   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
38   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
2           NY           N        1.0              1.0            08N   
20          NC           Y        1.0              1.0            03S   
26          VA           Y        1.0              1.0            124   
32          MA           N        1.0              1.0            08N   
38          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
2        08N             13.0               15A              15A   
20       03S             13.0               15A              15A   
26       124             13.0               15A              15A   
32       08N             13.0               15A              15A   
38       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
2              24.0            64.0               NaN  
20             24.0            64.0               NaN  
26             24.0            63.0               NaN  
32             24.0            64.0               NaN  
38             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2016  \
44491370  ES26136            0           19.0  ABSENTEE BY MAIL         Early   
44491376  ES26387            0           18.0  ABSENTEE BY MAIL         Early   
44491382  ES17204            0           50.0  ABSENTEE ONESTOP         Early   
44491388  ES26341            0           53.0         IN-PERSON  Election Day   
44491394  ES26380            0           61.0               NaN       No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491370      UNA           F        1997  2016-08-02         W          NL   
44491376      UNA           F        1998  2015-12-31         W          NL   
44491382      UNA           F        1966  2000-06-01         W          NL   
44491388      REP           F        1963  2015-11-30         W          NL   
44491394      UNA           F        1955  2015-12-18         W          NL   

          zip_code            res_street_address res_city_desc state_cd  \
44491370   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491376   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491382   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491388   28714.0       250  LAUREL ACRES RD       BURNSVILLE       NC   
44491394   28714.0  91 W BURNSVILLE CHURCH RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491370          NC           Y      100.0            100.0         02 CAN   
44491376          NC           Y      100.0            100.0         02 CAN   
44491382          FL           Y      100.0            100.0         02 CAN   
44491388          CO           Y      100.0            100.0         08 CRA   
44491394          NC           Y        NaN              NaN         01 BUR   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491370    02-CAN             11.0                24               24   
44491376    02-CAN             11.0                24               24   
44491382    02-CAN             11.0                24               24   
44491388    08-CRA             11.0                24               24   
44491394    01-BUR             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491370             47.0           118.0               NaN  
44491376             47.0           118.0               NaN  
44491382             47.0           118.0               NaN  
44491388             47.0           118.0               NaN  
44491394             47.0           118.0               NaN

In [22]:
# gen_2016.to_csv('Data/NC_gen_2016.zip', index=False)

### General 2014

In [23]:
## Make dataframe specific to 2014 general election
gen_2014 = get_election_df(2014)
print(len(gen_2014))
display(gen_2014.head())
gen_2014.tail()

4486408


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2014  \
3    AA56273            0           79.0         IN-PERSON  Election Day   
21   AA98377            0           38.0  ABSENTEE ONESTOP         Early   
27   AA69747            0           69.0         IN-PERSON  Election Day   
33  AA170513            0           66.0  ABSENTEE BY MAIL         Early   
39   BM49306            0           48.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
3       UNA           F        1935  1984-10-01         W          NL   
21      UNA           F        1976  1996-03-26         W          UN   
27      UNA           F        1945  1989-08-15         W          NL   
33      DEM           M        1948  2012-03-07         W          UN   
39      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
3    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
21   27215.0                    421  WHITT AVE       BURLINGTON       NC   
27   27215.0                    1013  EDITH ST       BURLINGTON       NC   
33   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
39   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
3           NY           N        1.0              1.0            08N   
21          NC           Y        1.0              1.0            03S   
27          VA           Y        1.0              1.0            124   
33          MA           N        1.0              1.0            08N   
39          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
3        08N             13.0               15A              15A   
21       03S             13.0               15A              15A   
27       124             13.0               15A              15A   
33       08N             13.0               15A              15A   
39       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
3              24.0            64.0               NaN  
21             24.0            64.0               NaN  
27             24.0            63.0               NaN  
33             24.0            64.0               NaN  
39             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2014  \
44491329  ES25745            0           58.0         IN-PERSON  Election Day   
44491335  ES25768            0           60.0               NaN       No Vote   
44491341  ES20237            0           62.0               NaN       No Vote   
44491365  ES17216            0           62.0  ABSENTEE ONESTOP         Early   
44491383  ES17204            0           48.0         IN-PERSON  Election Day   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491329      UNA           M        1956  2014-07-11         W          NL   
44491335      UNA           F        1954  2014-08-07         W          NL   
44491341      REP           M        1952  2004-09-27         W          UN   
44491365      UNA           M        1952  2000-06-15         W          NL   
44491383      UNA           F        1966  2000-06-01         W          NL   

          zip_code       res_street_address res_city_desc state_cd  \
44491329   28714.0        202  HAMLET DR       BURNSVILLE       NC   
44491335   28714.0        202  HAMLET DR       BURNSVILLE       NC   
44491341   28714.0          178  WREN DR       BURNSVILLE       NC   
44491365   28714.0  2156  LICKSKILLET RD       BURNSVILLE       NC   
44491383   28714.0  2156  LICKSKILLET RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491329          PA           Y      100.0            100.0         02 CAN   
44491335          IL           Y        NaN              NaN         02 CAN   
44491341          IL           N        NaN              NaN         01 BUR   
44491365          MI           Y      100.0            100.0         02 CAN   
44491383          FL           Y      100.0            100.0         02 CAN   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491329    02-CAN             11.0                24               24   
44491335    02-CAN             11.0                24               24   
44491341    01-BUR             11.0                24               24   
44491365    02-CAN             11.0                24               24   
44491383    02-CAN             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491329             47.0           118.0               NaN  
44491335             47.0           118.0               NaN  
44491341             47.0           118.0               NaN  
44491365             47.0           118.0               NaN  
44491383             47.0           118.0               NaN

In [24]:
# gen_2014.to_csv('Data/NC_gen_2014.zip', index=False)

### General 2012

In [7]:
## Make dataframe specific to 2012 general election
gen_2012 = get_election_df(2012)
print(len(gen_2012))
display(gen_2012.head())
gen_2012.tail()

4386614


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2012  \
4    AA56273            0           77.0         IN-PERSON  Election Day   
22   AA98377            0           36.0  ABSENTEE ONESTOP         Early   
28   AA69747            0           67.0  ABSENTEE ONESTOP         Early   
34  AA170513            0           64.0  ABSENTEE ONESTOP         Early   
40   BM49306            0           46.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
4       UNA           F        1935  1984-10-01         W          NL   
22      UNA           F        1976  1996-03-26         W          UN   
28      UNA           F        1945  1989-08-15         W          NL   
34      DEM           M        1948  2012-03-07         W          UN   
40      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
4    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
22   27215.0                    421  WHITT AVE       BURLINGTON       NC   
28   27215.0                    1013  EDITH ST       BURLINGTON       NC   
34   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
40   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
4           NY           N        1.0              1.0            08N   
22          NC           Y        1.0              1.0            03S   
28          VA           Y        1.0              1.0            124   
34          MA           N        1.0              1.0            08N   
40          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
4        08N             13.0               15A              15A   
22       03S             13.0               15A              15A   
28       124             13.0               15A              15A   
34       08N             13.0               15A              15A   
40       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
4              24.0            64.0               NaN  
22             24.0            64.0               NaN  
28             24.0            63.0               NaN  
34             24.0            64.0               NaN  
40             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2012  \
44491318  ES15279            0           51.0               NaN       No Vote   
44491324  ES13347            0           72.0         IN-PERSON  Election Day   
44491342  ES20237            0           60.0  ABSENTEE BY MAIL         Early   
44491366  ES17216            0           60.0  ABSENTEE ONESTOP         Early   
44491384  ES17204            0           46.0  ABSENTEE ONESTOP         Early   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491318      REP           M        1961  1996-10-11         W          NL   
44491324      DEM           F        1940  1990-09-28         W          NL   
44491342      REP           M        1952  2004-09-27         W          UN   
44491366      UNA           M        1952  2000-06-15         W          NL   
44491384      UNA           F        1966  2000-06-01         W          NL   

          zip_code        res_street_address res_city_desc state_cd  \
44491318   28714.0  508  HANNAH BRANCH RD       BURNSVILLE       NC   
44491324   28714.0  565  SHUFORD CREEK RD       BURNSVILLE       NC   
44491342   28714.0           178  WREN DR       BURNSVILLE       NC   
44491366   28714.0   2156  LICKSKILLET RD       BURNSVILLE       NC   
44491384   28714.0   2156  LICKSKILLET RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491318          NY           Y        NaN              NaN         09 SOU   
44491324          CA           N      100.0            100.0         09 SOU   
44491342          IL           N      100.0            100.0         01 BUR   
44491366          MI           Y      100.0            100.0         02 CAN   
44491384          FL           Y      100.0            100.0         02 CAN   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491318    09-SOU             11.0                24               24   
44491324    09-SOU             11.0                24               24   
44491342    01-BUR             11.0                24               24   
44491366    02-CAN             11.0                24               24   
44491384    02-CAN             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491318             47.0           118.0               NaN  
44491324             47.0           118.0               NaN  
44491342             47.0           118.0               NaN  
44491366             47.0           118.0               NaN  
44491384             47.0           118.0               NaN

In [8]:
# gen_2012.to_csv('Data/NC_gen_2012.zip', index=False)

In [11]:
OC_birth = voter_elecs.loc[voter_elecs['birth_state']=='OC']
OC_birth.loc[OC_birth['election_desc']=='11/03/2020 GENERAL'].head(100)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
108    DE236758  11/03/2020 GENERAL            1        NaN            NaN   
318    AA196723  11/03/2020 GENERAL            0        1.0      9169910.0   
342    AA148060  11/03/2020 GENERAL            0        1.0      9099437.0   
360    DL221658  11/03/2020 GENERAL            0        1.0      9192802.0   
366    AA202162  11/03/2020 GENERAL            0        1.0      9179739.0   
630    AA207681  11/03/2020 GENERAL            0        1.0      9189263.0   
846    AA201921  11/03/2020 GENERAL            0        NaN            NaN   
870    AA206220  11/03/2020 GENERAL            1        NaN            NaN   
918    AA196880  11/03/2020 GENERAL            0        1.0      9170173.0   
924    AA187630  11/03/2020 GENERAL            0        1.0      9154729.0   
948    AA168552  11/03/2020 GENERAL            0        NaN            NaN   
1020   AA181290  11/03/2020 GENERAL            0        1.0      9144279.0   
1662   EH964773  11/03/2020 GENERAL            0        1.0      9185339.0   
1782   AA180310  11/03/2020 GENERAL            0        NaN            NaN   
2154   AA120416  11/03/2020 GENERAL            0        1.0      9071173.0   
2160   AA200216  11/03/2020 GENERAL            0        1.0      9175808.0   
2298   AA196432  11/03/2020 GENERAL            1        NaN            NaN   
2316   BY569147  11/03/2020 GENERAL            0        1.0      9172397.0   
2496   AA142045  11/03/2020 GENERAL            0        1.0      9157792.0   
2988    AA90680  11/03/2020 GENERAL            0        1.0      9040871.0   
3036   AA188362  11/03/2020 GENERAL            1        NaN            NaN   
3042   AA183113  11/03/2020 GENERAL            0        NaN            NaN   
3048   AA168800  11/03/2020 GENERAL            0        1.0      9127070.0   
3144   AA182516  11/03/2020 GENERAL            0        NaN            NaN   
3180   AA188487  11/03/2020 GENERAL            0        1.0      9156262.0   
3186   AA168612  11/03/2020 GENERAL            1        NaN            NaN   
3210   AA191695  11/03/2020 GENERAL            0        NaN            NaN   
3216   AA167091  11/03/2020 GENERAL            0        1.0      9124590.0   
3234   AA149513  11/03/2020 GENERAL            0        1.0      9101416.0   
3252   AA150483  11/03/2020 GENERAL            0        NaN            NaN   
3294   AA202374  11/03/2020 GENERAL            0        1.0      9180181.0   
3366   AA158846  11/03/2020 GENERAL            0        1.0      9113671.0   
3372   AA161166  11/03/2020 GENERAL            0        1.0      9116493.0   
3408   AA208392  11/03/2020 GENERAL            0        1.0      9190261.0   
3414   AA208393  11/03/2020 GENERAL            0        1.0      9190262.0   
3444   DE147689  11/03/2020 GENERAL            0        1.0      9184552.0   
3546   BL340584  11/03/2020 GENERAL            0        1.0      9169821.0   
3564   AA164353  11/03/2020 GENERAL            0        1.0      9120625.0   
3570   AA200349  11/03/2020 GENERAL            0        1.0      9176068.0   
3594   AA216451  11/03/2020 GENERAL            0        1.0      9204580.0   
3600   AA207626  11/03/2020 GENERAL            0        1.0      9189148.0   
3702   AA205973  11/03/2020 GENERAL            1        NaN            NaN   
3726    AA95042  11/03/2020 GENERAL            0        1.0      9045315.0   
3732   AA102074  11/03/2020 GENERAL            0        1.0      9052513.0   
3798   AA200846  11/03/2020 GENERAL            0        1.0      9177012.0   
3816   AA202125  11/03/2020 GENERAL            0        1.0      9179647.0   
3828   AA203250  11/03/2020 GENERAL            0        1.0      9181750.0   
3858   DE285754  11/03/2020 GENERAL            0        1.0      9203567.0   
3900   AA187217  11/03/2020 GENERAL            0        1.0      9154084.0   
3912   AA217000  11/03/2020 GENERAL            0        1.0      9205566.0   
3960   AA155809  11/03/2020 GENER